In [2]:

# Load GPS data
# gps_data = pd.read_csv('MC2/gps.csv', parse_dates=['Timestamp'])

# # Load car assignment data
# car_assignment = pd.read_csv('MC2/car-assignments.csv')

# # Add a 'FullName' column to car assignment for easier reference
# car_assignment['FullName'] = car_assignment['FirstName'] + ' ' + car_assignment['LastName']

# # Merge GPS data with car assignment data
# merged_data = pd.merge(gps_data, car_assignment, left_on='id', right_on='CarID', how='left')

# # Sort the merged data by id and Timestamp
# merged_data = merged_data.sort_values(by=['id', 'Timestamp'])

# # Save the sorted merged data to a CSV file
# merged_data.to_csv('MC2/sorted_merged_gps_car_data.csv', index=False)

# print("Merged data sorted by id and time and saved successfully.")

import pandas as pd
import numpy as np
import ipywidgets as widgets
from ipywidgets import interact
from datetime import datetime, time
import plotly.graph_objects as go

# Load the sorted merged data from CSV
sorted_merged_data = pd.read_csv('MC2/sorted_merged_gps_car_data.csv', parse_dates=['Timestamp'])

# Separate truck drivers (those without CarID)
truck_drivers = sorted_merged_data[sorted_merged_data['CarID'].isna()]
drivers_with_cars = sorted_merged_data[~sorted_merged_data['CarID'].isna()]

# Date picker widget
date_picker = widgets.DatePicker(
    description='Select Date',
    disabled=False,
    value=datetime.strptime('2014-01-06', '%Y-%m-%d')
)

# Time picker widgets
start_time_picker = widgets.TimePicker(
    description='Start Time',
    value=time(0, 0),
    step=60
)

end_time_picker = widgets.TimePicker(
    description='End Time',
    value=time(23, 59),
    step=60
)

# Function to identify POIs where cars have stopped for more than 10 minutes
def identify_pois(data, stop_duration_minutes=5):
    pois = []
    grouped = data.groupby('id')
    
    for car_id, group in grouped:
        group = group.sort_values(by='Timestamp')
        group['time_diff'] = group['Timestamp'].diff().dt.total_seconds().div(60)  # Time difference in minutes
        
        # Identify stops longer than stop_duration_minutes
        stop_indices = np.where(group['time_diff'] >= stop_duration_minutes)[0]
        for idx in stop_indices:
            pois.append({
                'car_id': car_id,
                'FullName': group.iloc[idx]['FullName'],
                'FirstName': group.iloc[idx]['FirstName'],
                'LastName': group.iloc[idx]['LastName'],
                'lat': group.iloc[idx]['lat'],
                'long': group.iloc[idx]['long'],
                'stop_time': group.iloc[idx]['Timestamp'],
                'stop_duration': group.iloc[idx]['time_diff']
            })
    
    return pd.DataFrame(pois)

# Identify POIs for drivers with cars
pois = identify_pois(drivers_with_cars, stop_duration_minutes=5)

# Create a Plotly figure
fig = go.Figure()

# Function to filter and plot merged GPS data
def update_plot(date, start_time, end_time):
    start_datetime = datetime.combine(date, start_time)
    end_datetime = datetime.combine(date, end_time)
    
    # Filter merged data based on the selected date and time range
    filtered_data = drivers_with_cars[
        (drivers_with_cars['Timestamp'] >= start_datetime) & 
        (drivers_with_cars['Timestamp'] <= end_datetime)
    ]
    
    # Filter POIs based on the selected date and time range
    filtered_pois = pois[
        (pois['stop_time'] >= start_datetime) & 
        (pois['stop_time'] <= end_datetime)
    ]
    
    # Clear the existing data in the figure
    fig.data = []

    # Add new data to the figure
    for name, group in filtered_data.groupby('FullName'):
        fig.add_trace(go.Scatter(
            x=group['long'],
            y=group['lat'],
            mode='markers+lines',
            name=name,
            text=[f"{name}<br>{row['CurrentEmploymentType']}<br>{row['CurrentEmploymentTitle']}<br>{row['Timestamp']}<br>Lat: {row['lat']}, Long: {row['long']}" for i, row in group.iterrows()],
            hoverinfo='text'
        ))
    
    # Add POIs to the plot after the main data points
    fig.add_trace(
        go.Scatter(
            x=filtered_pois['long'],
            y=filtered_pois['lat'],
            mode='markers',
            marker=dict(color='red', size=10),
            name='POIs',
            text=filtered_pois.apply(lambda row: f"Car ID: {row['car_id']}<br>Person: {row['FirstName']} {row['LastName']}<br>Stop Time: {row['stop_time']}<br>Duration: {row['stop_duration']} mins<br>Lat: {row['lat']}, Long: {row['long']}", axis=1),
            hoverinfo='text'
        )
    )
    
    fig.update_layout(
        xaxis_title="Longitude",
        yaxis_title="Latitude",
        width=800,
        height=600
    )

    fig.show()

# Interactive plot
interact(update_plot, date=date_picker, start_time=start_time_picker, end_time=end_time_picker)



/var/folders/d4/nzg887ln1lgd3q6d2w7tbv5w0000gn/T/ipykernel_63726/4082900417.py:29: DtypeWarning: Columns (4,5,7,8,9) have mixed types. Specify dtype option on import or set low_memory=False.
  sorted_merged_data = pd.read_csv('MC2/sorted_merged_gps_car_data.csv', parse_dates=['Timestamp'])


interactive(children=(DatePicker(value=datetime.datetime(2014, 1, 6, 0, 0), description='Select Date', step=1)…

<function __main__.update_plot(date, start_time, end_time)>